# Import the necessary packages

In [1]:
import MDAnalysis as mda
import nglview as nv
import prolif as plf
import Bio
from pymol import cmd
import py3Dmol
import sys, os

/home/veronika/miniconda3/envs/binding_env/lib/python3.10/site-packages/MDAnalysis/topology/tables.py:52: DeprecationWarning: Deprecated in version 2.8.0
MDAnalysis.topology.tables has been moved to MDAnalysis.guesser.tables. This import point will be removed in MDAnalysis version 3.0.0
  warnings.warn(wmsg, category=DeprecationWarning)


In [2]:
import warnings
warnings.filterwarnings('ignore')

# Functions

### Downloading structures for PDB database

With Biopython:

In [3]:
from Bio.PDB import PDBList

def load_pdb_structure(pdb_id, file_format="pdb"):
    """
    Load a PDB structure by its ID from the PDB database.

    Parameters:
    - pdb_id: str, the four-letter PDB ID.
    - file_format: str, the format of the downloaded file (default is "pdb").

    Returns:
    - The path to the downloaded PDB file.
    """
    pdb_list = PDBList()
    pdb_filename = pdb_list.retrieve_pdb_file(pdb_id, pdir=".", file_format=file_format)
    return pdb_filename

In [4]:
# To parse the downloaded PDB file
from Bio.PDB import PDBParser

def parse_pdb_file(pdb_filename):
    parser = PDBParser()
    structure = parser.get_structure("Structure", pdb_filename)
    return structure

or with Pymol:

In [5]:
from pymol import cmd
def loading_structure(pdb_id, file_format='pdb'):
    """ 
    Loads a protein structure from the Protein Data Bank (PDB) and separates the protein from ligands.
    
    Parameters:
    - pdb_id (str): The four-letter PDB ID of the structure to fetch.
    - file_format (str): The format of the downloaded file (default is "pdb").
    
    Returns:
    - Saves the protein structure in .pdb format and ligand(s) in .mol2 format.
    """
    try:
        # Fetch the structure from PDB
        cmd.fetch(code=pdb_id, type=file_format)
        
        # Select protein chains
        cmd.select(name='Prot', selection='polymer.protein')
        
        # Select organic ligands
        cmd.select(name='Lig', selection='organic')
        
        # Save protein structure to a PDB file
        cmd.save(filename=f'{pdb_id}_clean.pdb', format='pdb', selection='Prot')
        
        # Save ligand structure to a MOL2 file
        cmd.save(filename=f'{pdb_id}_lig.mol2', format='mol2', selection='Lig')
        
        # Clear workspace to free memory
        cmd.delete('all')
        
        print(f"Structures saved: {pdb_id}_clean.pdb (protein), {pdb_id}_lig.mol2 (ligand)")
    
    except Exception as e:
        print(f"An error occurred: {e}")

### Uploading structure from current directory

With Biopython

In [6]:
def upload_structure(pdb_filename):
    parser = PDBParser()
    structure = parser.get_structure("Structure", pdb_filename)
    return structure

With Pymol

In [7]:
from pymol import cmd

def loading_structure_from_dir(structure_filename):
    """ 
    Loads a protein structure from a manually downloaded file and separates the protein from ligands.
    
    Parameters:
    - pdb_id (str): The four-letter PDB ID of the structure (used for naming output files).
    - file_format (str): The format of the local file (default is "pdb").
    
    Returns:
    - Saves the protein structure in .pdb format and ligand(s) in .mol2 format.
    """
    try:
        # Load the structure from local file (assuming filename is pdb_id.format)
        cmd.load(filename=structure_filename)
        
        # Select protein chains
        cmd.select(name='Prot', selection='polymer.protein')
        
        # Select organic ligands
        cmd.select(name='Lig', selection='organic')
        
        # Save protein structure to a PDB file
        cmd.save(filename=f'{pdb_id}_clean.pdb', format='pdb', selection='Prot')
        
        # Save ligand structure to a MOL2 file
        cmd.save(filename=f'{pdb_id}_lig.mol2', format='mol2', selection='Lig')
        
        # Clear workspace to free memory
        cmd.delete('all')
        
        print(f"Structures saved: {pdb_id}_clean.pdb (protein), {pdb_id}_lig.mol2 (ligand)")
    
    except Exception as e:
        print(f"An error occurred: {e}")

### Visualizing

With MDanalysis:

In [8]:
def parse_het_records(pdb_id):
        """Parse HET records from PDB file to identify ligands."""
        ligands = set()
        with open(f"pdb{pdb_id}.ent", 'r') as f:
            for line in f:
                if line.startswith('HET '):  # Note the space after HET
                    resname = line[7:10].strip()
                    ligands.add(resname)
                elif line.startswith('HETNAM'):
                    # Optional: Could store the full ligand names
                    pass
        ligand_resname = sorted(list(ligands))
        return ligand_resname

In [9]:
def mda_visual(pdb_id, ligand_resname):
    # Load PDB file
    u = mda.Universe(f"pdb{pdb_id}.ent")
    
    # Select protein and ligands
    protein = u.select_atoms("protein")
    ligands = [(name, u.select_atoms(f"resname {name}")) for name in ligand_resname]
    
    # Create visualization base
    view = nv.show_mdanalysis(protein)
    view.clear_representations()
    view.add_representation("surface", colorScheme="hydrophobicity")
    
    # Track ligand findings
    any_ligand_found = False
    
    for lig_name, lig in ligands:
        if lig.n_atoms > 0:
            # Add ligand to visualization
            lig_view = view.add_component(lig)
            lig_view.center()
            any_ligand_found = True
        else:
            print(f"Warning: No ligand {lig_name} found in {pdb_id}")
    
    if not any_ligand_found:
        print(f"No valid ligands found in {pdb_id}. Showing protein only.")
        
    return view

With Pymol3D:

In [10]:
def pymol3d_visual(pdb_id):
    view = py3Dmol.view()
    view.removeAllModels()
    view.setViewStyle({'style':'outline','color':'black','width':0.1})
    
    view.addModel(open(f'{pdb_id}_clean.pdb','r').read(),format='pdb')
    Prot=view.getModel()
    Prot.setStyle({'cartoon':{'arrows':True, 'tubes':True, 'style':'oval', 'color':'white'}})
    view.addSurface(py3Dmol.VDW,{'opacity':0.6,'color':'white'})
    
    
    view.addModel(open(f'{pdb_id}_lig.mol2','r').read(),format='mol2')
    ref_m = view.getModel()
    ref_m.setStyle({},{'stick':{'colorscheme':'greenCarbon','radius':0.2}})
    
    view.zoomTo()
    view.show()
    return view

# Examples

### Write your PDB ID and parse the structure

In [11]:
os.listdir()

['9fbd.pdb',
 '3vsk_clean.pdb',
 'pdb3vsk.ent',
 'auto_binding_vis.ipynb',
 '9fbd_lig.mol2',
 '3vsk_lig.mol2',
 '3vsk.pdb',
 '.ipynb_checkpoints',
 'pdb4hhb.ent',
 '9fbd_clean.pdb',
 'pdb9fbd.ent']

In [12]:
pdb_id = "3vsk"
pdb_filename = load_pdb_structure(pdb_id)
structure = parse_pdb_file(pdb_filename)

print(f"Parsed structure: {pdb_id}")

Structure exists: './pdb3vsk.ent' 
Parsed structure: 3vsk


or

In [23]:
pdb_id = "3vsk"
loading_structure(pdb_id)

Structures saved: 3vsk_clean.pdb (protein), 3vsk_lig.mol2 (ligand)


### Loading PDB to MDAnalysis

In [22]:
ligands = parse_het_records(pdb_id)
view = mda_visual(pdb_id, ligands)
view

NGLWidget()

In [16]:
view = pymol3d_visual(pdb_id)

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

### Complex

In [17]:
pdb_id = '9fbd'

In [18]:
pdb_filename = load_pdb_structure(pdb_id)
structure = parse_pdb_file(pdb_filename)

Structure exists: './pdb9fbd.ent' 


In [19]:
loading_structure(pdb_id)

Structures saved: 9fbd_clean.pdb (protein), 9fbd_lig.mol2 (ligand)


In [20]:
ligands = parse_het_records(pdb_id)
view = mda_visual(pdb_id, ligands)
view

NGLWidget()

In [21]:
view = pymol3d_visual(pdb_id)

3Dmol.js failed to load for some reason. Please check your browser console for error messages.